In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from pandas.api.types import is_numeric_dtype
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots
import datetime
from homebrewedFunctions.functions import *
import re
import multiprocess

In [2]:
all_keys = pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], low_memory =False).sort_index().keys()
pattern = re.compile(r'(\d+)^NAN(\d+)?$')

all_keys = [k for k in all_keys if not pattern.match(k)]
start_exp = all_keys.index("1EXPENDITURE")
start_debt = all_keys.index("1DEBT OUTSTANDING")
keys_dict = {"Revenues": all_keys[:start_exp],
            "Expenditures": [k for k in all_keys[start_exp:start_debt] if "CAPITAL OUTLAY" not in k] +["1CAPITAL OUTLAY"],
            "Debts": [k for k in all_keys[start_debt:] if "CAPITAL OUTLAY" not in k]}
            
stack_dfs = {"Expenditures": pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], usecols = ["State", "Year", "Format", "1GENERAL REVENUE", "1DEBT OUTSTANDING"] + keys_dict["Expenditures"], low_memory =False).sort_index(),
             "Revenues":pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], usecols = ["State", "Year", "Format", "1EXPENDITURE", "1DEBT OUTSTANDING"] + keys_dict["Revenues"], low_memory =False).sort_index(),
             "Debts":pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], usecols = ["State", "Year", "Format", "1EXPENDITURE", "1GENERAL REVENUE"] + keys_dict["Debts"], low_memory =False).sort_index()}

panel_dfs_dict = {}
for rev_exp in stack_dfs.keys():
    panel_dfs_dict[rev_exp] = {}
    for k in stack_dfs[rev_exp].index.get_level_values(2).unique():
        panel_dfs_dict[rev_exp][k] = stack_dfs[rev_exp][stack_dfs[rev_exp].index.get_level_values(2)==k].reset_index().set_index(["State","Year"]).sort_index()
        del panel_dfs_dict[rev_exp][k]["Format"]
    panel_dfs_dict[rev_exp] = {k.replace("amount", "finances"):panel_dfs_dict[rev_exp][k] for k in ["Local government amount",'State & local government amount', 'State government amount']}

for key, dct in panel_dfs_dict.items():
    for k, df in dct.items():
        for col in df.columns:
            if is_numeric_dtype(df[col]):
                df[col] = df[col].fillna(0)

            else:
                try:
                    print(col, "forced")

                    df[col] = pd.to_numeric(df[col], errors = "coerce").fillna(0).astype(float)
                except:
                    # print(col, "skipped")
                    pass
        if key == "Revenues":
            df["1TOTAL INCOME"] = df["1INDIVIDUAL INCOME"].add(df["1CORPORATE INCOME"])
            df["1PROPERTY AND SPECIAL ASSESSMENTS"] = df[["1PROPERTY", "1SPECIAL ASSESSMENTS"]].sum(axis = 1)
            df["1DEFICIT"] = df["1EXPENDITURE"].sub(df["1GENERAL REVENUE"])
        if key == "Debts":
            df["1NET INDEBTEDNESS"] = df["1DEBT OUTSTANDING"].sub(df["1OTHER THAN INSURANCE TRUST FUNDS"])
            
        # warning indicates that copying dataframe will defragment it;
        #  not sure if this actually fixes the problem
        df = df.copy()                
cpi_code = {"CPI":"CPIAUCSL"}
start = datetime.datetime(1947,1,1)
end = datetime.datetime.now()
cpi = gather_data(cpi_code, start, end, freq = "A").reset_index().rename(columns = {"DATE": "Year"})
cpi["Year"] = pd.to_datetime(cpi["Year"].astype(str).str[:4], format = "%Y")
cpi["Year"] = cpi["Year"].astype(str)
cpi.set_index("Year", inplace = True)
cpi["CPI"] = cpi["CPI"].div(cpi["CPI"].iloc[-2]).astype(float)
efnagdp = pd.read_csv("EFNAGDPTaxes.csv", parse_dates = ["Year"]).set_index(["State", "Year"]).sort_index()


def set_plot_dfs(panel_dfs_dict, keys, efnagdp, cpi):
    # keys = ["1" + k for k in keys]
    plot_dfs = {}
    for key in panel_dfs_dict.keys():
        plot_dfs[key] = {}
        plot_dfs[key]["Level"] = panel_dfs_dict[key].mul(10**3).copy()
        plot_dfs[key]["Level"].rename(columns = {k:k.replace("1", "").title() for k in plot_dfs[key]["Level"].keys()}, inplace = True)
    #     plot_dfs[key]["Level"]["Total Income"] = plot_dfs[key]["Level"]["Individual Income"].add(plot_dfs[key]["Level"]["Corporate Income"])
    #     plot_dfs[key]["Level"]["Property and Special Assessments"] = plot_dfs[key]["Level"][["Property", "Special Assessments"]].sum(axis = 1)
        plot_dfs[key]["Level"]["GDP"] = efnagdp["GDP"]
        plot_dfs[key]["Level"]["Deficit"] = plot_dfs[key]["Level"]["Expenditure"].sub(plot_dfs[key]["Level"]["General Revenue"])
        plot_dfs[key]["Real Level"] = plot_dfs[key]["Level"].div(cpi["CPI"], level = "Year", axis = 0)
        plot_dfs[key]["Level"]["Population"] = efnagdp["Population"]
        plot_dfs[key]["Percent of General Revenue"] = plot_dfs[key]["Level"].apply(lambda x: pd.to_numeric(x).div(plot_dfs[key]["Level"]["General Revenue"]).mul(100))    
        plot_dfs[key]["Percent of Expenditure"] = plot_dfs[key]["Level"].apply(lambda x: pd.to_numeric(x).div(plot_dfs[key]["Level"]["Expenditure"]).mul(100))    
        plot_dfs[key]["Percent of GDP"] = plot_dfs[key]["Level"].apply(lambda x: pd.to_numeric(x).div(plot_dfs[key]["Level"]["GDP"]).mul(100))
        
        plot_dfs[key]["Real Value Per Capita"] = plot_dfs[key]["Real Level"].apply(lambda x: pd.to_numeric(x).div(plot_dfs[key]["Level"]["Population"]))    
        for k in plot_dfs[key].keys():
            plot_dfs[key][k]["EFNA"] = efnagdp["EFNA"]
            plot_dfs[key][k]["Unemployment Rate"] = efnagdp["Unemployment Rate"]
            plot_dfs[key]["Level"]["Population"] = efnagdp["Population"]

    return plot_dfs
plot_dfs = {}

for key in panel_dfs_dict.keys():
    plot_dfs[key] = set_plot_dfs(panel_dfs_dict[key], keys_dict[key], efnagdp, cpi)


import os
for revexp_key in plot_dfs.keys():
    for key in plot_dfs[revexp_key].keys():
        try:
            os.mkdir(f"outputs/{key}")
        except:
            pass

regions_df = pd.read_csv("USCensusRegions.csv")#.set_index("State")
scatter_figs = {}
for revexp_key in plot_dfs.keys():
    for key, p_dfs in plot_dfs[revexp_key].items():
        for p_dfskey, df in p_dfs.items():
            map_figs = {}
            title = f"{key}<br>{revexp_key}: {p_dfskey}"
            html_path = f"outputs/{key}/ScatterPlots{revexp_key}{key}{p_dfskey}.html"
            create_scatter_dropdown(df, regions_df=regions_df,
                                    title = title,
                                    filename = html_path, 
                                    show_fig = False)
            for name in df.keys():
                map_figs[name] = create_map(df.reset_index(), name, title = title,time_name = "Year")
            combined_map_fig = combine_map_figs(map_figs, title)
            html_path = f"outputs/{key}/MapPlots{revexp_key}{key}{p_dfskey}.html"
            combined_map_fig.write_html(html_path)

for revexp_key in plot_dfs.keys():
    for key, p_dfs in plot_dfs[revexp_key].items():
        # figs = {k: line_dropdown(dataframe, regions_df) for k, dataframe in p_dfs.items()}
        # fig = dict_of_line_figs_to_dropdown_fig(figs, show_fig = False, use_sliders = True)
        filename = f"outputs/{key}/LinePlotsStateFinances{revexp_key}{key}.html"
        title = f"{key}<br>{revexp_key}"
        fig = aggregated_line_dropdown(p_dfs, regions_df, title = title)
        fig.write_html(filename, config=dict(displayModeBar=True))

1INTERGOVERNMENTAL EXPENDITURE forced
1ASSISTANCE AND SUBSIDIES forced
1INSURANCE BENEFITS AND REPAYMENTS forced
2EDUCATION forced
1HIGHER EDUCATION forced
1ELEMENTARY & SECONDARY forced
1OTHER EDUCATION forced
1LIBRARIES forced
1CASH ASSISTANCE PAYMENTS forced
1VENDOR PAYMENTS forced
2HOSPITALS forced
1EMPLOYMENT SECURITY ADMINISTRATION forced
1VETERANS' SERVICES forced
2AIR TRANSPORTATION (AIRPORTS) forced
2PARKING FACILITIES forced
2SEA AND INLAND PORT FACILITIES forced
1FIRE PROTECTION forced
1CORRECTION forced
2SEWERAGE forced
2SOLID WASTE MANAGEMENT forced
1MISCELLANEOUS COMMERCIAL ACTIVITIES forced
1UTILITY EXPENDITURE forced
2WATER SUPPLY forced
2ELECTRIC POWER forced
2GAS SUPPLY forced
2TRANSIT forced
1LIQUOR STORE EXPENDITURE forced
1INSURANCE TRUST EXPENDITURE forced
2UNEMPLOYMENT COMPENSATION forced
2EMPLOYEE RETIREMENT forced
2WORKERS' COMPENSATION forced
1OTHER INSURANCE TRUST forced
1INTERGOVERNMENTAL EXPENDITURE forced
1ASSISTANCE AND SUBSIDIES forced
1INSURANCE BENEFIT

In [3]:
start_year = 2005
areas = {"Revenues":{"Revenue Source by Government" : ["General Revenue From Own Sources", "From Federal Government", "From State Government", "From Local Governments"],
                    "Taxes": ["Intergovernmental Revenue", 'Property', 'Sales And Gross Receipts',
                              'Individual Income', 'Corporate Income', 'Motor Vehicle License', 'Other Taxes', 
                              'Current Charges', 'Interest Earnings', 'Special Assessments', 'Sale Of Property', 'Other General Revenue']},
        "Expenditures": {
            "Expenditures":[
                "Intergovernmental Expenditure", "Current Operations", "Capital Outlay",
                "Assistance And Subsidies", "Interest On Debt", "Insurance Benefits And Repayments"],
            "Expenditure by Function": [
                    "Intergovernmental Expenditure", "Education", "Libraries", "Public Welfare", "Hospitals", 
                    "Health", "Employment Security Administration", "Veterans' Services",
                    "Highways", "Air Transportation (Airports)", "Parking Facilities", "Sea And Inland Port Facilities",
                    "Police Protection", "Fire Protection", "Correction", "Protective Inspection And Regulation",
                    "Natural Resources", "Parks And Recreation", "Housing And Community Development", "Sewerage",
                    "Solid Waste Management", "Financial Administration","Judicial And Legal", "General Public Buildings",
                    "Other Governmental Administration", "Interest On General Debt", "Miscellaneous Commercial Activities",
                    "Other And Unallocable", "Utility Expenditure", "Liquor Store Expenditure", "Insurance Trust Expenditure"]},
            # "Debt": {""}
}
figs = {}
for revexp_key in areas.keys():
    for key, p_dfs in plot_dfs[revexp_key].items():
        figs[key] = {}
        for form, plot_df in p_dfs.items():# ["Level", "Real Level", "Percent of General Revenue", "Percent of GDP", "Real Value Per Capita"]:
            figs[key][form] = {}
            df = plot_df.copy()
            df.rename(columns = {k:k.replace("1", "").replace("2","").title() for k in df.keys()}, inplace = True)
            df = df.reset_index().melt(id_vars=["State","Year"],
                var_name="Name", 
                value_name="Value",
                )
            df = df.set_index(["State", "Year"])#.round(4)
            states = df.index.get_level_values("State").unique()

            for components_group, components in areas[revexp_key].items():


                figs[key][form][components_group] = {}

                for state in states:
                    plot_df = df.loc[state].reset_index()#.loc[start_year:].reset_index()
                    plot_df = plot_df[plot_df["Name"].isin(components)].dropna()
                    plot_df["Value"] = pd.to_numeric(plot_df["Value"])
                    title = f"<br>{key}<br>{form}: {state}<br>"
                    px_fig = px.area(
                        plot_df, x="Year", y="Value", color="Name")
                    px_fig.update_layout(title = dict(text = title,x = 0, xanchor = "left", yanchor = "bottom",y = 1),
                                         legend_title_text = components_group),
                    
                    figs[key][form][components_group][state] = px_fig
                figs[key][form][components_group]  = dict_of_figs_to_dropdown_fig(figs[key][form][components_group], 
                                                                                show_fig = False,
                                                                                use_sliders = True)
                figs[key][form][components_group].write_html(f"outputs/{key}/AreaPlots{revexp_key}{key}{form}{components_group}.html")
                

In [4]:
url = "https://www.fraserinstitute.org/sites/default/files/economic-freedom-of-north-america-2022-for-website-allgovs.xlsx"
storage_options = {'User-Agent': 'Mozilla/5.0'}
efna = pd.read_excel(url, storage_options=storage_options, sheet_name=None)
efnagdp = pd.read_csv("EFNAGDPTaxes.csv", parse_dates = ["Year"]).set_index(["State", "Year"]).sort_index()

In [5]:
def omit_variables(dct_of_dfs, omit):
    dct_of_dfs = dct_of_dfs[~dct_of_dfs.index.get_level_values("Name").isin(omit)].dropna()
    return dct_of_dfs
income = pd.read_csv("PersonalIncomeStateData/CAINC5N__ALL_AREAS_2001_2022.csv", encoding="latin1", low_memory=False)
income["State"] = income["GeoName"].str.extract(r"([A-Z]{2})")
income["GeoFIPS"] = income["GeoFIPS"].str.replace('"', '')
income['StateFIPS'] = income["GeoFIPS"].str.extract(r"(\d{2})")
income["CountyFIPS"] = income["GeoFIPS"].str[-3:].astype(str)
income["County"] = income["GeoName"].str.split(",").str[0]
income.dropna(subset = ["State"], inplace = True)
income.rename(columns = {"Description": "Name"}, inplace = True)

for year in range(2001, 2023):
    year = str(year)
    income[year] = pd.to_numeric(income[year], errors = "coerce")
    income[year][income["Unit"] == income["Unit"].unique()[0]] = income[year][income["Unit"] == income["Unit"].unique()[0]].mul(10**3)

income["Unit"] = income["Unit"].str.replace("Thousands of dollars", "Dollars")
for orig_str, new_str in {"Thousands of dollars": "Dollars", "thousands of dollars": "Dollars", "dollars": "Dollars"}.items():
    income["Name"] = income["Name"].str.replace(orig_str, new_str)
income["Name"] = income["Name"].str.rstrip()
income_names = income["Name"].unique()

melt_df = income[["State", "County", "Name", "Unit"] + [str(y) for y in range(2001,2023)]].melt(id_vars=["State", "County", "Name", "Unit"], var_name="Year", value_name="Value")
melt_df = melt_df.set_index(["State", "County", "Name", "Year"])[["Value"]]
melt_df["Value"] = pd.to_numeric(melt_df["Value"], errors = "coerce")
state_income = melt_df.groupby(["State", "Year", "Name"]).sum()
# state_income["Value"][state_income.index.get_level_values("Name") == "Per capita personal income (Dollars)"] = state_income["Value"][state_income.index.get_level_values("Name") == "Personal income (Dollars)"].values / state_income["Value"][state_income.index.get_level_values("Name") == "Population (persons) 2/"].values
pi_dfs = {k: state_income.copy() for k in ["Level", "Real Level", "Percent of Personal Income", "Real Value Per Capita"]}
cpi_str_index = cpi.reset_index().copy()
cpi_str_index["Year"] = cpi_str_index["Year"].astype(str).str[:4]
cpi_str_index.set_index("Year", inplace = True)
pi_dfs["Real Level"]["Value"] = pi_dfs["Level"]["Value"].div(cpi_str_index["CPI"], level = "Year", axis = 0)
pi_dfs["Real Level"]["Value"] = omit_variables(pi_dfs["Real Level"]["Value"], ["Population (persons) 2/"])
pi_dfs["Percent of Personal Income"]["Value"] = state_income["Value"].div(state_income["Value"].xs("Personal income (Dollars)", level = "Name")).mul(100)
pi_dfs["Percent of Personal Income"]["Value"] = omit_variables(pi_dfs["Percent of Personal Income"]["Value"], 
                                                               ["Per capita personal income (Dollars)", "Population (persons) 2/"])
pi_dfs["Real Value Per Capita"]["Value"] = pi_dfs["Real Level"]["Value"].div(state_income["Value"].xs("Population (persons) 2/", level = "Name"))
pi_dfs["Real Value Per Capita"]["Value"] = omit_variables(pi_dfs["Real Value Per Capita"]["Value"], 
                                                          ["Per capita personal income (Dollars)", "Population (persons) 2/"])

/tmp/ipykernel_51991/167200927.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_51991/167200927.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_51991/167200927.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_51991/167200927.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pyd

In [6]:
try:
    os.mkdir("outputs/PersonalIncome")
except:
    pass
names = list(pi_dfs["Level"].index.get_level_values("Name").unique())
names = [n for n in names if "    " not in n]
areas = {str(i):{} for i in range(3, -1, -1)}
for num_spaces in areas.keys():
    areas[num_spaces] = [n for n in names if " " * int(num_spaces) in n[:int(num_spaces)]]
    names= [n for n in names if n not in areas[num_spaces] ]
    
figs = {}
key = "Personal Income"

for form, plot_df in pi_dfs.items():# ["Level", "Real Level", "Percent of General Revenue", "Percent of GDP", "Real Value Per Capita"]:
    figs[form] = {}
    df = plot_df.copy()

    states = df.index.get_level_values("State").unique()

    for components_group, components in areas.items():
        figs[form][components_group] = {}
        for state in states:
            plot_df = df.loc[state].reset_index()#.loc[start_year:].reset_index()
            plot_df = plot_df[plot_df["Name"].isin(components)].dropna()
            plot_df["Value"] = pd.to_numeric(plot_df["Value"])
            title_key = f"{components_group} {key}<br>{form}<br>{state}"
            px_fig = px.area(
                plot_df, x="Year", y="Value", color="Name", title = title_key)

            figs[form][components_group][state] = px_fig
        figs[form][components_group]  = dict_of_figs_to_dropdown_fig(figs[form][components_group], 
                                                                        show_fig = False,
                                                                        use_sliders = True)
        figs[form][components_group].write_html(f"outputs/PersonalIncome/AreaPlots{key}{form}{components_group}.html".replace(" ", ""))

In [7]:
pi_keys = {k:[n for n in income_names if n in v.dropna().index.get_level_values("Name").unique()] for k, v in pi_dfs.items()}
pi_dfs = {k:v.reset_index().pivot_table(index=['State', 'Year'], columns='Name', values='Value')[pi_keys[k]] for k,v in pi_dfs.items()}


scatter_figs = {}
for key, df in pi_dfs.items():
    title = f"Personal Income<br>{key}"
    map_figs = {}

    html_path = f"outputs/PersonalIncome/ScatterPlotsPersonalIncome{key}.html"
    create_scatter_dropdown(df, regions_df=regions_df, title = title,
                            filename = html_path,  
                            show_fig = False)
    for name in df.keys():
        map_figs[name] = create_map(df.reset_index(), name, time_name = "Year", title=title)
    combined_map_fig = combine_map_figs(map_figs, title = title)
    html_path = f"outputs/PersonalIncome/MapPlotsPersonalIncome{key}.html"
    combined_map_fig.write_html(html_path)

regions_df = pd.read_csv("USCensusRegions.csv")#.set_index("State")
filename = f"outputs/PersonalIncome/LinePlotsStatePI.html"
fig = aggregated_line_dropdown(pi_dfs, regions_df)
fig.write_html(filename, config=dict(displayModeBar=True))

Name State  Year  Personal income (Dollars)  Population (persons) 2/  \
0       AK  2001               2.128712e+10                 633714.0   
1       AK  2002               2.233147e+10                 642337.0   
2       AK  2003               2.337214e+10                 648414.0   
3       AK  2004               2.442916e+10                 659286.0   
4       AK  2005               2.601962e+10                 666946.0   
...    ...   ...                        ...                      ...   
1117    WY  2018               3.402519e+10                 574801.0   
1118    WY  2019               3.559260e+10                 575341.0   
1119    WY  2020               3.786637e+10                 577605.0   
1120    WY  2021               4.086656e+10                 579483.0   
1121    WY  2022               4.258471e+10                 581381.0   

Name  Per capita personal income (Dollars)  Earnings by place of work  \
0                                 817038.0               1.702

In [8]:
efna_description = efna["Index Components"]["The Areas and Components of the Economic Freedom of North America Index"].dropna()
codes = efna_description.str[:3]
for char in [":", "."]: 
    codes = codes.str.replace(char, "")
maxef = 6
codes = "EFNA " + codes
efna["Index Components"]["Code"] = codes.str.strip()
efna_description = efna["Index Components"].copy().dropna()
efna_description = efna_description[~(efna_description["Code"].str.contains("i")| efna_description["Code"].str.contains("v"))]
efna_description.rename(columns = {"The Areas and Components of the Economic Freedom of North America Index": "Description"}, inplace = True)
efna_description.set_index("Code", inplace = True)
efna_description.loc["EFNA 2B"] = '2B. Top Marginal Income Tax Rate Attributes'
keys = list(efnagdp.keys())
end_index = keys.index(f"EFNA {maxef}")
efna_df = efnagdp[keys[3:end_index+1]]
efna_df = efna_df.dropna(how = "all", axis = 0)
efna_sub_keys = {f"EFNA {i}":[k for k in efna_df.keys() if f"EFNA {i}" in k and "i" not in k] for i in range(1,maxef+1)}
for i in range(1,7):
    efna_df[f"EFNA {i}"] = efna_df[efna_sub_keys[f"EFNA {i}"]].mean(axis = 1).round(3)
efna_sub_keys["Major EFNA Components"] = [f"EFNA {i}" for i in range(maxef+1)]



In [9]:
try:
    os.mkdir("outputs/EFNA")
except:
    pass
figs = {}

for key, keys in efna_sub_keys.items():
    if len(keys) > 1:
        components_group = key
        components = keys
        figs[components_group] = {}
        df = efna_df.copy()
        df = df.reset_index().melt(id_vars=["State","Year"],
            var_name="Name", 
            value_name="Value",
            )
        df = df.set_index(["State", "Year"])#.round(4)
        states = df.index.get_level_values("State").unique()

        for state in states:
            plot_df = df.loc[state].reset_index()#.loc[start_year:].reset_index()
            plot_df = plot_df[plot_df["Name"].isin(components)].dropna().sort_values("Name")
            plot_df["Name"] = plot_df["Name"].apply(lambda x: efna_description.loc[x]["Description"])
            plot_df["Value"] = pd.to_numeric(plot_df["Value"]).div(len(components))
            title_key = f"{components_group} <br>{state}"
            px_fig = px.area(
                plot_df, x="Year", y="Value", color="Name", title = title_key)

            figs[components_group][state] = px_fig
        figs[components_group]  = dict_of_figs_to_dropdown_fig(figs[components_group], 
                                                                        show_fig = False,
                                                                        use_sliders = True)
        figs[components_group].write_html(f"outputs/EFNA/AreaPlots{components_group}.html")
plot_df = pd.pivot_table(df.reset_index(), index = ["State", "Year"], columns = "Name", values = "Value")
map_figs = {}
for name in plot_df.keys():
    map_figs[name] = create_map(plot_df.reset_index(), name, time_name = "Year", title=name)

combined_map_fig = combine_map_figs(map_figs, title = key)
html_path = f"outputs/EFNA/MapPlotsEFNA.html"
combined_map_fig.write_html(html_path)

/home/jamescaton/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/home/jamescaton/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/home/jamescaton/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the 

In [10]:
# regions_df = pd.read_csv("USCensusRegions.csv")#.set_index("State")
rename_df = efna["Index Components"]["The Areas and Components of the Economic Freedom of North America Index"].dropna()
rename_df.index = "EFNA " + rename_df.str.split(" ").str[0].str.replace(":", "").str.replace(".","")
rename_df.loc["EFNA 2B"] = '2B. Top Marginal Income Tax Rate Attributes'
plot_df = efna_df.rename(columns = {k:rename_df.loc[k] for k in rename_df.iloc[1:].index})
fig = line_dropdown(plot_df.sort_index(axis =1), regions_df)
fig.write_html("outputs/EFNA/EFNALinePlot.html")


/home/jamescaton/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

